# Hafta 3: Özellik Mühendisliği ve Seçimi

**Dersin Hedefleri:**
1.  Özellik mühendisliğinin (Feature Engineering) makine öğrenmesi pipeline'ındaki merkezi rolünü anlamak.
2.  Farklı veri tipleri (sayısal, kategorik, zaman damgalı) için yaygın özellik türetme tekniklerini uygulamak.
3.  Eksik verileri (missing data) işlemek için stratejiler geliştirmek ve test etmek.
4.  Özellik seçimi (feature selection) yöntemlerinin amacını ve temel türlerini öğrenmek.
5.  Görselleştirmenin, özellik mühendisliği sürecindeki keşif ve doğrulama rolünü kullanmak.

## 1. Özellik Mühendisliği Nedir?

"Garbage in, garbage out" (Çöp girer, çöp çıkar) makine öğrenmesindeki en temel prensiplerden biridir. Bir modelin performansı, ne kadar karmaşık veya güçlü olursa olsun, büyük ölçüde kendisine verilen verinin kalitesine ve anlamlılığına bağlıdır.

**Özellik Mühendisliği:** Ham veriyi, bir makine öğrenmesi modelinin problem çözme yeteneğini en üst düzeye çıkaracak bir formata dönüştürme sanatı ve bilimidir. Bu süreç, **domain bilgisi**, **yaratıcılık** ve **istatistiksel titizliğin** bir birleşimidir.

İyi tasarlanmış özellikler:
- Modelin veri içindeki desenleri (patterns) daha kolay öğrenmesini sağlar.
- Daha basit modellerin bile yüksek performans göstermesine olanak tanır.
- Modelin yorumlanabilirliğini artırabilir.

## 2. Pratik Uygulamalar: Sayısal ve Kategorik Özellikler

Bu bölümde, bir e-ticaret şirketinin müşteri veritabanını temsil eden sentetik bir veri seti üzerinde çalışacağız.

### Sentetik Veri Üretimi

Müşteri demografik bilgilerini, son aktivitelerini ve harcama alışkanlıklarını içeren gerçekçi bir veri seti oluşturalım.

In [ ]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from datetime import datetime, timedelta

# Veri üretimi için fonksiyon
def generate_customer_data(num_customers=1000):
    """Generates a synthetic customer dataset."""
    np.random.seed(42)
    
    customer_ids = range(1, num_customers + 1)
    
    # Demografik özellikler
    ages = np.random.randint(18, 70, size=num_customers)
    # Bazı yaş değerlerini eksik bırakalım
    ages = [age if np.random.rand() > 0.1 else np.nan for age in ages]
    
    cities = np.random.choice(['Istanbul', 'Ankara', 'Izmir', 'Bursa', 'Antalya'], 
                              size=num_customers, 
                              p=[0.4, 0.2, 0.2, 0.1, 0.1])
    
    # Kayıt tarihi
    end_date = datetime.now()
    start_date = end_date - timedelta(days=3*365)
    registration_dates = [start_date + timedelta(seconds=np.random.randint(0, int((end_date - start_date).total_seconds()))) for _ in range(num_customers)]
    
    # Harcama bilgileri
    total_spent = np.random.gamma(2, 150, size=num_customers).round(2)
    # Yaş ile harcama arasında hafif bir pozitif korelasyon ekleyelim
    total_spent += np.array([age * 1.5 if not np.isnan(age) else 0 for age in ages])
    
    # Son görülme (eksik değerler içerebilir)
    last_seen_days_ago = np.random.randint(0, 365, size=num_customers)
    last_seen_days_ago = [d if np.random.rand() > 0.15 else np.nan for d in last_seen_days_ago]
    
    # Hedef değişken (Churn olup olmadığı)
    churn_probability = 1 / (1 + np.exp(-( (np.array(last_seen_days_ago, dtype=float) / 365 * 2) - (total_spent / 500) )))
    churn = (np.random.rand(num_customers) < churn_probability).astype(int)

    
    df = pd.DataFrame({
        'customer_id': customer_ids,
        'age': ages,
        'city': cities,
        'registration_date': registration_dates,
        'total_spent': total_spent,
        'last_seen_days_ago': last_seen_days_ago,
        'churn': churn
    })
    
    return df

customer_df = generate_customer_data(500)
print("Veri Seti Önizlemesi:")
display(customer_df.head())
print("\nVeri Seti Bilgileri:")
customer_df.info()

### 2.1. Eksik Veri İşleme (Missing Data Imputation)

Modellerin çoğu, eksik (`NaN`) değerlerle çalışamaz. Bu değerleri stratejik olarak doldurmamız gerekir.

**Stratejiler:**
- **Sayısal Değerler:** Ortalama (mean), medyan (median) veya belirli bir sabit (örn: 0) ile doldurma. Medyan, aykırı değerlere (outliers) karşı daha dayanıklıdır.
- **Kategorik Değerler:** En sık tekrar eden değer (mode) veya "Bilinmiyor" gibi yeni bir kategori ile doldurma.

In [ ]:
# Eksik değerlerin görselleştirilmesi
plt.figure(figsize=(10, 6))
sns.heatmap(customer_df.isnull(), cbar=False, cmap='viridis')
plt.title('Eksik Değerlerin Konumu')
plt.show()

# Sayısal 'age' sütunu için medyan ile doldurma
age_median = customer_df['age'].median()
customer_df['age'].fillna(age_median, inplace=True)

# 'last_seen_days_ago' için de medyan kullanalım
last_seen_median = customer_df['last_seen_days_ago'].median()
customer_df['last_seen_days_ago'].fillna(last_seen_median, inplace=True)

print("Eksik değerler doldurulduktan sonraki durum:")
customer_df.info()

### 2.2. Kategorik Veri Kodlama (Categorical Encoding)

Modeller matematiksel işlemler yapar ve metin tabanlı kategorileri ('Istanbul', 'Ankara' vb.) doğrudan anlayamaz. Bunları sayısallaştırmamız gerekir.

**One-Hot Encoding:** En yaygın yöntemdir. Her bir kategori için yeni bir ikili (0/1) sütun oluşturur. `pandas.get_dummies()` ile kolayca uygulanabilir.

In [ ]:
# 'city' sütununa one-hot encoding uygulama
city_dummies = pd.get_dummies(customer_df['city'], prefix='city', drop_first=True)
# drop_first=True: Multicollinearity'yi önlemek için bir referans kategori atar.

# Yeni oluşturulan sütunları ana dataframe ile birleştirme
customer_df = pd.concat([customer_df, city_dummies], axis=1)

# Orijinal 'city' sütununu kaldırabiliriz
customer_df.drop('city', axis=1, inplace=True)

print("One-Hot Encoding sonrası DataFrame:")
display(customer_df.head())

### 2.3. Zaman Damgalı Özellikler (Date/Time Features)

`registration_date` gibi tarih sütunları, doğrudan model için anlamsızdır. Ancak içlerinden çok değerli bilgiler çıkarabiliriz.

In [ ]:
# 'registration_date' sütununu datetime objesine çevirelim (eğer değilse)
customer_df['registration_date'] = pd.to_datetime(customer_df['registration_date'])

# Yeni özellikler türetme
customer_df['registration_year'] = customer_df['registration_date'].dt.year
customer_df['registration_month'] = customer_df['registration_date'].dt.month
customer_df['registration_day_of_week'] = customer_df['registration_date'].dt.dayofweek # Pazartesi=0, Pazar=6

# Üyelik süresi (üyeliğin ne kadar eski olduğu)
customer_df['membership_days'] = (datetime.now() - customer_df['registration_date']).dt.days

# Orijinal tarih sütununu kaldırabiliriz
customer_df.drop('registration_date', axis=1, inplace=True)

print("Tarih özellikleri eklendikten sonra DataFrame:")
display(customer_df[['customer_id', 'registration_year', 'registration_month', 'registration_day_of_week', 'membership_days']].head())

### Alıştırma 1: Etkileşim Özellikleri (Interaction Features)

Bazen iki veya daha fazla özelliğin birleşimi, tek başlarına olduklarından daha fazla bilgi taşır. Bunlara **etkileşim özellikleri** denir.

1.  `customer_df` DataFrame'ine `spent_per_day` adında yeni bir özellik ekleyin. Bu özellik, `total_spent` değerinin `membership_days` değerine bölünmesiyle hesaplanmalıdır. (Not: `membership_days` 0 ise ne yapılacağını düşünün, 0'a bölme hatasını önleyin!).
2.  Bu yeni özelliğin `churn` ile olan ilişkisini görselleştirin. Örneğin, `churn` durumuna göre `spent_per_day` dağılımını bir kutu grafiği (`boxplot`) veya keman grafiği (`violinplot`) ile çizin. Bu özellik, churn'ü tahmin etmede faydalı görünüyor mu?

In [ ]:
# Alıştırma 1 için çözüm alanı
# 1. spent_per_day özelliğini oluştur
customer_df['spent_per_day'] = customer_df['total_spent'] / (customer_df['membership_days'] + 1e-6) # 0'a bölmeyi önle

# 2. Görselleştirme
plt.figure(figsize=(12, 7))
sns.boxplot(x='churn', y='spent_per_day', data=customer_df)
plt.title('Günlük Harcama vs. Churn Durumu')
plt.ylim(0, customer_df['spent_per_day'].quantile(0.95)) # Aykırı değerleri görselden çıkarmak için
plt.show()

## 3. Özellik Seçimi (Feature Selection)

Çok fazla özellik eklemek her zaman iyi değildir. Bazı özellikler gürültü yaratabilir, modelin eğitilmesini yavaşlatabilir ve "Boyutsallık Laneti" (Curse of Dimensionality) problemine yol açabilir.

**Özellik Seçimi:** Model performansını en üst düzeye çıkarmak için en anlamlı ve en bilgilendirici özellik alt kümesini seçme işlemidir.

### Filtre Yöntemleri (Filter Methods)

Bu yöntemler, özellikleri modelden bağımsız olarak, sadece istatistiksel özelliklerine göre sıralar veya filtreler. Hızlı ve basittirler. En yaygın olanı, hedef değişken ile olan **korelasyonu** incelemektir.

In [ ]:
# Model için son hazırlık: Hedef değişkeni ve ID'yi ayıralım
X = customer_df.drop(['churn', 'customer_id'], axis=1)
y = customer_df['churn']

# Tüm özelliklerin hedef değişken (churn) ile olan korelasyonunu hesapla
correlations = X.corrwith(y).sort_values(ascending=False)

plt.figure(figsize=(10, 8))
sns.barplot(x=correlations.values, y=correlations.index)
plt.title('Özelliklerin Churn ile Korelasyonu')
plt.xlabel('Korelasyon Katsayısı')
plt.show()

print("Korelasyon Değerleri:")
print(correlations)

# Yorum: `last_seen_days_ago` ve `membership_days` churn'ü tahmin etmede en güçlü sinyallere sahip görünüyor.
# Bu, domain bilgisiyle de tutarlıdır (uzun süredir uğramayan veya yeni olan müşterilerin churn etme olasılığı daha yüksek olabilir).

### Alıştırma 2: Korelasyon Matrisi

Sadece özelliklerin hedefle değil, birbirleriyle olan ilişkileri de önemlidir. Yüksek oranda korele olan iki özellik (örn. > 0.90) genellikle modele aynı bilgiyi verir ve bu durum multicollinearity gibi sorunlara yol açabilir.

1. `X` DataFrame'indeki tüm özelliklerin birbirleriyle olan korelasyonunu hesaplayın (`.corr()` metodu).
2. Bu korelasyon matrisini bir ısı haritası (`heatmap`) kullanarak görselleştirin.
3. Birbirleriyle çok yüksek korelasyona sahip özellik çiftleri var mı? Varsa, bunlardan birini modelden çıkarmayı düşünür müydünüz? Neden?

In [ ]:
# Alıştırma 2 için çözüm alanı

# 1. Tüm özelliklerin birbirleriyle olan korelasyonunu hesaplama
correlation_matrix = X.corr()

# 2. Korelasyon matrisini ısı haritası ile görselleştirme
plt.figure(figsize=(14, 10))
sns.heatmap(correlation_matrix, annot=True, fmt='.2f', cmap='coolwarm', 
            center=0, square=True, linewidths=1, cbar_kws={"shrink": 0.8})
plt.title('Özelliklerin Birbirleriyle Korelasyon Matrisi', fontsize=14)
plt.tight_layout()
plt.show()

# 3. Yüksek korelasyonlu özellik çiftlerini bulma (eşik: 0.90)
high_corr_threshold = 0.90
high_corr_pairs = []

for i in range(len(correlation_matrix.columns)):
    for j in range(i+1, len(correlation_matrix.columns)):
        if abs(correlation_matrix.iloc[i, j]) > high_corr_threshold:
            high_corr_pairs.append({
                'Feature 1': correlation_matrix.columns[i],
                'Feature 2': correlation_matrix.columns[j],
                'Correlation': correlation_matrix.iloc[i, j]
            })

if high_corr_pairs:
    print("\nYüksek Korelasyonlu Özellik Çiftleri (|korelasyon| > 0.90):")
    for pair in high_corr_pairs:
        print(f"  - {pair['Feature 1']} <-> {pair['Feature 2']}: {pair['Correlation']:.3f}")
    print("\nYorum: Çok yüksek korelasyonlu özellik çiftlerinden birini modelden çıkarmayı düşünebiliriz.")
    print("Bu, multicollinearity'yi azaltır ve modelin daha kararlı ve yorumlanabilir olmasını sağlar.")
    print("Genellikle domain bilgisi veya hedef değişkenle daha düşük korelasyona sahip olanı çıkarırız.")
else:
    print("\nYüksek Korelasyonlu Özellik Çifti Bulunamadı (|korelasyon| > 0.90)")
    print("\nYorum: Veri setimizde çok yüksek korelasyonlu özellik çiftleri yok.")
    print("Ancak, 0.70-0.90 arasındaki korelasyonlar da dikkat edilmesi gereken durumlardır.")
    print("Bu durumda, tüm özellikleri modelde tutabiliriz veya regularizasyon teknikleri kullanabiliriz.")

## 4. Explainable Boosting Machine (EBM): Yorumlanabilir Özellik Seçimi

**EBM (Explainable Boosting Machine)**, Microsoft Research tarafından geliştirilen, hem yüksek performans hem de tam yorumlanabilirlik sunan bir Generalized Additive Model (GAM) türüdür.

### EBM Nedir?

Klasik makine öğrenmesi modellerinde genellikle bir **trade-off** vardır:
- **Basit modeller** (Linear Regression, Decision Trees): Yorumlanabilir ama düşük performans
- **Karmaşık modeller** (Random Forest, XGBoost, Neural Networks): Yüksek performans ama "black box"

**EBM bu trade-off'u kırma iddiasındadır.** Gradient Boosting kadar güçlüdür, ancak tamamen yorumlanabilirdir.

### Temel Özellikler:
1. **Glasbox Model**: Her özelliğin katkısı ayrı ayrı görselleştirilebilir
2. **Doğrusal Olmayan İlişkiler**: Her özellik için karmaşık, doğrusal olmayan şekil fonksiyonları öğrenir
3. **Otomatik Etkileşim Tespiti**: Özellikler arası etkileşimleri (interactions) otomatik bulur ve modelleyebilir
4. **Feature Importance**: Hangi özelliklerin önemli olduğunu kesin olarak gösterir
5. **Local & Global Explanations**: Hem genel model davranışını hem de tek bir tahmini açıklayabilir

### 4.1. Matematiksel Temel: GAM ve Boosting'in Birleşimi

EBM, şu matematiksel yapıya dayanır:

$$g(E[y]) = \beta_0 + \sum_{i=1}^{n} f_i(x_i) + \sum_{i,j} f_{ij}(x_i, x_j)$$

**Basitçe açıklarsak:**
- $g()$: Link fonksiyonu (classification için logit, regression için identity)
- $\beta_0$: Intercept (başlangıç değeri)
- $f_i(x_i)$: Her bir özelliğin **bireysel shape fonksiyonu** (non-linear olabilir)
- $f_{ij}(x_i, x_j)$: İki özellik arasındaki **pairwise etkileşim fonksiyonu**

**Neden yorumlanabilir?**
Her terim ($f_i$) ayrı ayrı hesaplanır ve görselleştirilebilir. Model, her özelliğin tahmini **nasıl etkilediğini** bize gösterir.

**Nasıl eğitiliyor?**
1. **Round-robin Boosting**: Her iterasyonda, bir özellik seçilir
2. O özellik için küçük bir düzeltme (residual fit) yapılır
3. Süreç, tüm özellikler için tekrarlanır (cyclic)
4. Bu, yüzlerce/binlerce kez tekrar eder

Bu yaklaşım, özelliklerin birbirinden bağımsız katkılarını öğrenmeyi sağlar.

### 4.2. Ana Kısıtlamalar ve Dikkat Edilmesi Gerekenler

**1. Etkileşim Limiti**
- EBM varsayılan olarak sadece **pairwise (ikili) etkileşimleri** modeller
- 3'lü veya daha fazla özellik etkileşimi desteklenmez
- Çok karmaşık etkileşimler için deep learning gerekebilir

**2. Büyük Veri Setlerinde Performans**
- Boosting iteratif olduğu için eğitim **yavaş** olabilir (XGBoost'tan daha yavaş)
- 100K+ satır ve 50+ özellikte eğitim saatler sürebilir
- GPU desteği yok (sadece CPU)

**3. Kategorik Özelliklerde Dikkat**
- Çok fazla kategoriye sahip özellikler (high cardinality) problemli olabilir
- One-hot encoding ile özellik sayısı patlaması yaşanabilir
- EBM kategorik değişkenleri otomatik işleyebilir ama dikkatli kullanılmalı

**4. Overfitting Riski**
- Çok fazla boosting iteration ile model ezberleyebilir
- `max_rounds`, `learning_rate`, `max_leaves` gibi hiperparametrelerin dikkatli ayarlanması gerekir
- Validation set kullanarak early stopping önemli

**5. Yorumlanabilirlik vs. Performans**
- Bazı durumlarda XGBoost veya Neural Network daha iyi performans verebilir
- EBM'in avantajı yorumlanabilirlik; eğer yorumlanabilirlik gerekli değilse, en iyi seçim olmayabilir

### 4.3. EBM ile Churn Tahmini: Pratik Uygulama

Şimdi, hazırladığımız müşteri veri seti üzerinde EBM kullanarak:
1. Model eğitimi yapacağız
2. Özelliklerin önemini göreceğiz
3. Her özelliğin tahmini nasıl etkilediğini görselleştireceğiz
4. En önemsiz özellikleri elimine edeceğiz

In [ ]:
# EBM kütüphanesini yükle
#!pip install -q interpret

In [ ]:
# Gerekli kütüphaneleri import et
from interpret.glassbox import ExplainableBoostingClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score, accuracy_score, classification_report

# Veriyi train ve test olarak böl
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)

print(f"Train set: {X_train.shape[0]} örneklem")
print(f"Test set: {X_test.shape[0]} örneklem")
print(f"Özellik sayısı: {X_train.shape[1]}")

In [ ]:
# EBM modelini oluştur ve eğit
ebm = ExplainableBoostingClassifier(
    random_state=42,
    interactions=5,  # En iyi 10 pairwise etkileşimi otomatik bul
    max_rounds=5000,  # Boosting iterasyon sayısı
    learning_rate=0.01,  # Öğrenme hızı
    early_stopping_rounds=50  # Validation set'te 50 round boyunca iyileşme olmazsa dur
)

# Modeli eğit
ebm.fit(X_train, y_train)

# Test seti üzerinde tahmin yap
y_pred = ebm.predict(X_test)
y_pred_proba = ebm.predict_proba(X_test)[:, 1]

# Model performansını değerlendir
print("Model Performansı:")
print(f"Accuracy: {accuracy_score(y_test, y_pred):.4f}")
print(f"ROC-AUC: {roc_auc_score(y_test, y_pred_proba):.4f}")
print("\nClassification Report:")
print(classification_report(y_test, y_pred))

#### Global Feature Importance: Hangi Özellikler En Önemli?

EBM'in en güçlü özelliklerinden biri, her bir özelliğin modeldeki **global katkısını** kesin olarak gösterebilmesidir.

In [ ]:
# Global açıklamayı al
from interpret import show

ebm_global = ebm.explain_global()

# Jupyter'da interaktif gösterim
show(ebm_global)

In [ ]:
# Feature importance'ı manuel olarak görselleştirelim
feature_importances = ebm_global.data()['scores']
feature_names = ebm_global.data()['names']

# DataFrame'e dönüştür ve sırala
importance_df = pd.DataFrame({
    'Feature': feature_names,
    'Importance': feature_importances
}).sort_values('Importance', ascending=False)

# Görselleştir
plt.figure(figsize=(10, 8))
plt.barh(importance_df['Feature'][:15], importance_df['Importance'][:15])
plt.xlabel('Global Importance Score')
plt.title('Top 15 Özellik Önemi (EBM)')
plt.gca().invert_yaxis()
plt.tight_layout()
plt.show()

print("Tüm Özelliklerin Önem Skorları:")
print(importance_df)

#### Shape Fonksiyonları: Özelliklerin Tahmini Nasıl Etkiliyor?

EBM'in en değerli özelliği: Her bir özelliğin değerinin, tahmin üzerindeki **doğrusal olmayan etkisini** görebiliriz.

In [ ]:
# En önemli 4 özelliğin shape fonksiyonlarını görselleştir
top_features = importance_df['Feature'][:4].tolist()

fig, axes = plt.subplots(2, 2, figsize=(14, 10))
axes = axes.ravel()

for idx, feature in enumerate(top_features):
    # Özelliğin index'ini bul
    feature_idx = list(X.columns).index(feature) if feature in X.columns else None
    
    if feature_idx is not None:
        # Shape verilerini al
        feature_data = ebm_global.data(feature_idx)
        
        # Grafik çiz
        axes[idx].plot(feature_data['names'][1:], feature_data['scores'], marker='o', linewidth=2)
        axes[idx].axhline(y=0, color='red', linestyle='--', alpha=0.3)
        axes[idx].set_title(f'{feature}', fontsize=12, fontweight='bold')
        axes[idx].set_xlabel('Feature Value')
        axes[idx].set_ylabel('Log-odds Contribution')
        axes[idx].grid(True, alpha=0.3)

plt.tight_layout()
plt.show()

#### Pairwise Etkileşimler: Hangi Özellikler Birlikte Çalışıyor?

EBM, iki özellik arasındaki etkileşimleri otomatik tespit eder ve modelleyebilir.

In [ ]:
# Etkileşimleri bul
interaction_features = [name for name in feature_names if ' x ' in name]
interaction_scores = [importance_df[importance_df['Feature'] == name]['Importance'].values[0] 
                      for name in interaction_features]

# Etkileşimleri görselleştir
if interaction_features:
    interaction_df = pd.DataFrame({
        'Interaction': interaction_features,
        'Importance': interaction_scores
    }).sort_values('Importance', ascending=False)
    
    print("Tespit Edilen Pairwise Etkileşimler:")
    print(interaction_df)
    
    # Grafik
    plt.figure(figsize=(10, 6))
    plt.barh(interaction_df['Interaction'][:5], interaction_df['Importance'][:5])
    plt.xlabel('Importance Score')
    plt.title('Top 10 Pairwise Etkileşimler')
    plt.gca().invert_yaxis()
    plt.tight_layout()
    plt.show()
else:
    print("Model hiçbir anlamlı pairwise etkileşim tespit etmedi.")

#### Local Explanation: Tek Bir Tahminin Açıklanması

EBM, sadece global değil, **local (bireysel) açıklamalar** da yapabilir. Yani "Bu müşteri neden churn edecek?" sorusuna yanıt verebilir.

In [ ]:
# Test setinden bir örnek seç
sample_idx = 5
sample = X_test.iloc[sample_idx:sample_idx+1]

# Local açıklama
ebm_local = ebm.explain_local(X_test, y_test)

# İnteraktif gösterim (Jupyter'da çalışır)
show(ebm_local, sample_idx)

#### Feature Elimination: Önemsiz Özellikleri Çıkaralım

Şimdi, önem skorlarına dayanarak **düşük katkılı özellikleri** modelden çıkaralım ve performansı karşılaştıralım.

In [ ]:
# Eşik değeri belirle: Importance < 0.01 olan özellikleri çıkar
importance_threshold = 0.01

# Çıkarılacak özellikleri belirle (sadece main features, interactions hariç)
low_importance_features = importance_df[
    (importance_df['Importance'] < importance_threshold) & 
    (~importance_df['Feature'].str.contains(' x '))
]['Feature'].tolist()

print(f"Çıkarılacak {len(low_importance_features)} özellik:")
print(low_importance_features)

# Yeni özellik seti oluştur
X_train_reduced = X_train.drop(columns=low_importance_features)
X_test_reduced = X_test.drop(columns=low_importance_features)

print(f"\nÖnceki özellik sayısı: {X_train.shape[1]}")
print(f"Yeni özellik sayısı: {X_train_reduced.shape[1]}")

In [ ]:
# Yeni model eğit
ebm_reduced = ExplainableBoostingClassifier(
    random_state=42,
    interactions=10,
    max_rounds=5000,
    learning_rate=0.01,
    early_stopping_rounds=50
)

ebm_reduced.fit(X_train_reduced, y_train)

# Performansı değerlendir
y_pred_reduced = ebm_reduced.predict(X_test_reduced)
y_pred_proba_reduced = ebm_reduced.predict_proba(X_test_reduced)[:, 1]

print("Özellik Eliminasyonu Sonrası Model Performansı:")
print(f"Accuracy: {accuracy_score(y_test, y_pred_reduced):.4f}")
print(f"ROC-AUC: {roc_auc_score(y_test, y_pred_proba_reduced):.4f}")

# Karşılaştırma
print("\n" + "="*50)
print("KARŞILAŞTIRMA:")
print("="*50)
print(f"Önceki Model - Özellik: {X_train.shape[1]}, ROC-AUC: {roc_auc_score(y_test, y_pred_proba):.4f}")
print(f"Yeni Model   - Özellik: {X_train_reduced.shape[1]}, ROC-AUC: {roc_auc_score(y_test, y_pred_proba_reduced):.4f}")
print(f"\nPerformans Farkı: {roc_auc_score(y_test, y_pred_proba_reduced) - roc_auc_score(y_test, y_pred_proba):.4f}")

#### Alıştırma 3: EBM ile Deney Yapın

1. `importance_threshold` değerini değiştirerek (örn: 0.05, 0.02, 0.005) farklı özellik sayılarıyla model eğitin
2. Her durumda ROC-AUC skorunu kaydedin ve karşılaştırın
3. Optimal özellik sayısını bulun (en az özellik, en yüksek performans)
4. **Bonus:** En önemli 5 özelliği kullanarak yeni bir model eğitin ve performansı karşılaştırın

In [ ]:
# Alıştırma 3 için çözüm alanı

### 4.4. EBM ile Öğrendiklerimiz: Özet

**EBM'in Avantajları:**
1. ✅ Tam yorumlanabilirlik: Her özelliğin katkısını kesin olarak görebiliriz
2. ✅ Yüksek performans: Gradient Boosting seviyesinde doğruluk
3. ✅ Otomatik etkileşim tespiti: Manuel feature engineering yükünü azaltır
4. ✅ Objektif özellik seçimi: Hangi özelliklerin önemli olduğunu kesin olarak biliyoruz

**Ne Zaman EBM Kullanmalıyız?**
- Modelin kararlarını açıklamamız gerektiğinde (regülasyon, sağlık, finans)
- Özellik mühendisliği ve seçimi için veri keşfi yaparken
- Domain uzmanlarına model davranışını göstermek istediğimizde

**Ne Zaman Dikkatli Olmalıyız?**
- Çok büyük veri setlerinde (eğitim yavaş olabilir)
- 3+ özellik etkileşimleri gerektiğinde
- Yorumlanabilirlik öncelik değilse (XGBoost/NN daha hızlı olabilir)

### Haftanın Özeti

Bu hafta, ham veriyi modelin anlayabileceği ve en iyi şekilde öğrenebileceği bir formata dönüştürdük.
- Eksik veri, kategorik veri ve zaman damgalı veri gibi yaygın zorluklarla nasıl başa çıkılacağını öğrendik.
- Yaratıcı bir şekilde yeni özellikler (etkileşim, oran vb.) türetmenin önemini anladık.
- Görselleştirmenin, özelliklerin değerini anlamada ne kadar güçlü bir araç olduğunu gördük.
- Korelasyon gibi basit filtre yöntemleriyle en bilgilendirici özellikleri nasıl seçebileceğimize dair bir başlangıç yaptık.

### Sonraki Adımlar

Artık temizlenmiş ve zenginleştirilmiş bir özellik setimiz var. Bir sonraki hafta, bu özellik setini kullanarak bir model eğiteceğiz. Ancak bunu rastgele yapmayacağız. **Hafta 4: MLOps Prensipleri ve Deney Yönetimi**'nde, her bir model eğitimini, farklı parametreler ve özellik setleriyle yapılan, takip edilebilir ve karşılaştırılabilir bir deneye nasıl dönüştüreceğimizi öğreneceğiz. `MLflow` gibi araçlarla tanışacağız.

---

## **Hafta 4: MLOps Prensipleri ve Deney Yönetimi**```python